# Capstone Project – Finding Best Places to open new Chinese Restaurant

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## 1- Introduction <a name="introduction"></a>

Toronto is a Large Metropoly with diverse population. This diversity also means a diversity in cuture. As any other large multicultural city, Toronto has high demand for cultural food to satisfy its population.

With this in mind we seek to find the best place for new culture restaurants. In this example we will use Chinese food as a guideline, but this core idea can be used for any other cuisine or service.

First we have to address our problems and goals:
* List all Chinese Restaurant in Toronto and each neighborhood
* Find places where ther is lacking nearby Chinese Restaurant
* Find places for potential new Chinese Restaurant

## 2- Data <a name="data"></a>

For this example, I will use Toronto as baseline, but it can be use with any city that exist in Foursquare database.

I will use more venues' informations than previous projects, such as price, popularity, if its clean or if its require any dress code. 

Following data sources will be needed to extract/generate the required information:
* centers of areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* information about restaurants as their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Toronto's neighborhoods will be obtained using **Google Maps API geocoding**

### Finding all neighborhoods

For this part we will find all neighborhoods in Toronto and it's latitude and longitude coordinates.

In [ ]:
pip install geopy folium

In [94]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [8]:
CLIENT_ID = 'K1NJ4WQH0IQ1M2RQ3F3AUUYWK2H5DUBH2IPIGYB4FQ3Y2GPK' # your Foursquare ID
CLIENT_SECRET = 'J1K0L5M5J22KM403ZQOGLIV5R2ZGQBFRRJUGFRISQCJURHVZ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Credentials Saved')

Credentials Saved


In [147]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="tor_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

GeocoderServiceError: Non-successful status code 502

Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Toronto. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in meters).


In [70]:
!pip install shapely pyproj

     |████████████████████████████████| 1.0 MB 2.1 MB/s eta 0:00:01
     |████████████████████████████████| 7.5 MB 302 kB/s eta 0:00:01     |█▉                              | 419 kB 1.6 MB/s eta 0:00:05     |█████████▊                      | 2.3 MB 1.6 MB/s eta 0:00:04     |██████████████████████████████▍ | 7.1 MB 6.8 MB/s eta 0:00:01


In [74]:
import shapely.geometry

import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Toronto center longitude={}, latitude={}'.format(longitude, latitude))
x, y = lonlat_to_xy(longitude, latitude)
print('Toronto center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Toronto center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Toronto center longitude=-79.3839347, latitude=43.6534817
Toronto center UTM X=-5310527.241020994, Y=10507538.454385541
Toronto center longitude=-79.3839347000005, latitude=43.653481699999766


<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)


In [75]:
tor_x, tor_y = lonlat_to_xy(longitude, latitude) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = tor_x - 6000
x_step = 600
y_min = tor_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(tor_x, tor_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

...

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:


In [81]:
map_candidates = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.Marker([latitude,longitude], popup='Alexanderplatz').add_to(map_candidates)
for lat, lon in zip(latitudes, longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_candidates) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_candidates)
#     folium.Marker([lat, lon]).add_to(map_candidates)
map_candidates

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Toronto Town Hall.


In [87]:
def get_address(latitude, longitude):
    try:
        address = geolocator.reverse([latitude,longitude])
        return address
    except:
        return None

addr = get_address(latitude, longitude)
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(latitude, longitude, addr))

<class 'str'>
Reverse geocoding check
-----------------------
Address of [43.6534817, -79.3839347] is: Toronto City Hall, 100, Queen Street West, Financial District, Spadina—Fort York, Old Toronto, Toronto, Golden Horseshoe, Ontario, M5H 2N2, Canada


In [88]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = str(address).replace(', Canada', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [89]:
df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  Richard L. Hearn Thermal Generating Station (c...  43.646210 -79.333368   
1  Portlands Energy Centre, 470, Unwin Avenue, To...  43.649935 -79.333929   
2  Toronto Hydro, Commissioners Street, Toronto—D...  43.653661 -79.334490   
3  Revival Film Studios, 629, Eastern Avenue, Les...  43.657386 -79.335052   
4  67, Winnfred Avenue, Leslieville, Toronto—Danf...  43.661112 -79.335613   
5  98, Bertmount Avenue, Leslieville, Toronto—Dan...  43.664839 -79.336175   
6  78, Galt Avenue, Leslieville, Toronto—Danforth...  43.668565 -79.336736   
7  Regatta Road, Toronto—Danforth, Old Toronto, T...  43.640269 -79.336968   
8  Unwin Avenue, Port Lands, Toronto—Danforth, Ol...  43.643994 -79.337530   
9  Basin Street, Toronto—Danforth, Old Toronto, T...  43.647719 -79.338091   

              X             Y  Distance from center  
0 -5.312327e+06  1.050182e+07           5992.495307  
1 -5.311727e+06  1.050182e+07           5840.376700  
2 -5.311127e+06  1.050182e+07           5747.173218  
3 -5.310527e+06  1.050182e+07           5715.767665  
4 -5.309927e+06  1.050182e+07           5747.173218  
5 -5.309327e+06  1.050182e+07           5840.376700  
6 -5.308727e+06  1.050182e+07           5992.495307  
7 -5.313227e+06  1.050234e+07           5855.766389  
8 -5.312627e+06  1.050234e+07           5604.462508  
9 -5.312027e+06  1.050234e+07           5408.326913

...and let's now save/persist this data into local file.


In [90]:
df_locations.to_pickle('./locations.pkl')

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Chinese restaurant' category, as we need info on Chinese restaurants in the neighborhood.

In [96]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

chinese_restaurant_categories = ['4bf58dd8d48988d145941735','52af3a5e3cf9994f4e043bea','52af3a723cf9994f4e043bec',
                                 '52af3a7c3cf9994f4e043bed','58daa1558bbb0b01f18ec1d3','52af3a673cf9994f4e043beb',
                                 '52af3a903cf9994f4e043bee','4bf58dd8d48988d1f5931735','52af3a9f3cf9994f4e043bef',
                                 '52af3aaa3cf9994f4e043bf0','52af3ab53cf9994f4e043bf1','52af3abe3cf9994f4e043bf2',
                                 '52af3ac83cf9994f4e043bf3','52af3ad23cf9994f4e043bf4','52af3add3cf9994f4e043bf5',
                                 '52af3af23cf9994f4e043bf7','52af3ae63cf9994f4e043bf6','52af3afc3cf9994f4e043bf8',
                                 '52af3b053cf9994f4e043bf9','52af3b213cf9994f4e043bfa','52af3b293cf9994f4e043bfb',
                                 '52af3b343cf9994f4e043bfc','52af3b3b3cf9994f4e043bfd','52af3b463cf9994f4e043bfe',
                                 '52af3b633cf9994f4e043c01','52af3b513cf9994f4e043bff','52af3b593cf9994f4e043c00',
                                 '52af3b6e3cf9994f4e043c02','52af3b773cf9994f4e043c03','52af3b813cf9994f4e043c04',
                                 '52af3b893cf9994f4e043c05','52af3b913cf9994f4e043c06','52af3b9a3cf9994f4e043c07',
                                 '52af3ba23cf9994f4e043c08']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Deutschland', '')
    address = address.replace(', Germany', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [100]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    chinese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, CLIENT_ID, CLIENT_SECRET, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_chinese = is_restaurant(venue_categories, specific_filter=chinese_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_chinese, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_chinese:
                    chinese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, chinese_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
chinese_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('chinese_restaurants_350.pkl', 'rb') as f:
        chinese_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, chinese_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(chinese_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . .

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


 .

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This

 .

...

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This

 .

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This

 . done.


<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


In [102]:
print('Total number of restaurants:', len(restaurants))
print('Total number of Chinese restaurants:', len(chinese_restaurants))
print('Percentage of Chinese restaurants: {:.2f}%'.format(len(chinese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1175
Total number of Chinese restaurants: 59
Percentage of Chinese restaurants: 5.02%
Average number of restaurants in neighborhood: 5.063186813186813


In [103]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4bc1df994cdfc9b6a3229521', "Gale's Snack Bar", 43.658239, -79.339077, '539 Eastern Ave (Carlaw Ave), Toronto ON, Canada', 92, False, -5310340.672131852, 10502272.900043106)
('539a1eff498e1bf8518e4eb5', 'Food Dudes Pantry', 43.65630014845779, -79.3382027627999, '24 Carlaw Ave (at Lake Shore Blvd E), Toronto ON M4M 2R7, Canada', 315, False, -5310660.2536905715, 10502205.67661057)
('53af0086498eb15122135e6a', 'Completo', 43.66255039511819, -79.33404945763401, '5 Coady Ave (at Queen St E), Toronto ON M4M 2Y9, Canada', 306, False, -5309718.197581599, 10501617.04816121)
('4ec03c1329c25ce5a22fca40', 'Ascari Enoteca', 43.66205431604801, -79.33545691089822, '1111 Queen St. E (at Caroline Ave.), Toronto ON M4M 1K7, Canada', 315, False, -5309779.349025334, 10501788.261534175)
('4ada456ff964a520c22021e3', 'Hanoi 3 Seasons', 43.662199311171825, -79.33457571173595, '1135 Queen Street East (Larchmount Ave), Toronto ON, Canada', 320, False, -5309767.41

In [104]:
print('List of Chinese restaurants')
print('---------------------------')
for r in list(chinese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(chinese_restaurants))

List of Chinese restaurants
---------------------------
('55f07a51498ef8afddf53c9c', 'Mean Bao', 43.659232, -79.348011, '181 Carlaw Ave (Queen & Carlaw), Toronto ON M4M 2S1, Canada', 314, True, -5310069.543551475, 10503287.667968202)
('5137cd7de4b011df3fcf0ca0', 'Dumpling House 餃子園', 43.66572519110226, -79.35117791892397, '619 Gerrard St East (at Broadview Ave), Toronto ON, Canada', 312, True, -5308996.296522276, 10503540.080450712)
('4bb7dee07421a5933632c140', 'Phoenix Bakery', 43.66568719069107, -79.35139459318192, '346 Broadview Ave, Toronto ON M4M 2G9, Canada', 299, True, -5308999.59483436, 10503565.768366132)
('58ab6f3eea29b818ab66cb3e', 'Wok & Roast Chinese BBQ', 43.665067, -79.352298, '349 Broadview Ave (Gerrard St E), Toronto ON M4M 2H1, Canada', 292, True, -5309086.807856108, 10503680.939916573)
('4cc45369be40a35d26c87d4c', 'New Pepper Chili Szechuan Restaurant', 43.66541287557503, -79.35247679960533, '368 Broadview Ave. (Gerrard), Toronto ON, Canada', 253, True, -5309029.5128

In [105]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: 
Restaurants around location 104: Cluck Clucks, Miyaki Sushi, Pita Land
Restaurants around location 105: Mangia and Bevi Resto-Bar, Fusaro's, Ardo, Mengrai Gourmet Thai, Pita Land, Oriental Taste, Nari Sushi
Restaurants around location 106: Sukhothai, Souvlaki Express, Ontario Restaurant, Mengrai Gourmet Thai, Oriental Taste, King Solomon Queen Of Sheba, Lime Sushi
Restaurants around location 107: Sukhothai, Ontario Restaurant, The Local Gest, Sultan Of Samosas, Pho U, Jerk Paradise
Restaurants around location 108: Kingyo Toronto, Zakkushi ざっ串, Kanpai Snack Bar, The Pear Tree, Hey Lucy, Thai Room - Carlton, The Local Gest, China Gourmet
Restaurants around location 109: Cranberries, F'Amelia, Murgatroid, Kingyo Toronto, Butter Chicken Factory, Tender Trap Restaurant, Suruthis Take Out, Cabbage Town Kitchen
Restaurants around locatio

In [107]:
map_toronto = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.Marker([latitude,longitude], popup='Town Hall').add_to(map_toronto)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_chinese = res[6]
    color = 'red' if is_chinese else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_toronto)
map_toronto

Looking good. So now we have all the restaurants in area within few kilometers from Toronto Town Hall, and we know which ones are Chinese restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Chinese restaurant!


## 3- Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Toronto that have low restaurant density, particularly those with low number of Chinese restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required data: location and type (category) of every restaurant within 6km from Toronto Town Hall. We have also identified Chinese restaurants (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of 'restaurant density' across different areas of Toronto - we will use heatmaps to identify a few promising areas close to center with low number of restaurants in general (and no Chinese restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create clusters of locations that meet some basic requirements established in discussion with stakeholders: we will take into consideration locations with no more than two restaurants in radius of 250 meters, and we want locations without Chinese restaurants in radius of 400 meters. We will present map of all such locations but also create clusters (using k-means clustering) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.


## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [108]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 5.063186813186813


Address   Latitude  Longitude  \
0  Richard L. Hearn Thermal Generating Station (c...  43.646210 -79.333368   
1  Portlands Energy Centre, 470, Unwin Avenue, To...  43.649935 -79.333929   
2  Toronto Hydro, Commissioners Street, Toronto—D...  43.653661 -79.334490   
3  Revival Film Studios, 629, Eastern Avenue, Les...  43.657386 -79.335052   
4  67, Winnfred Avenue, Leslieville, Toronto—Danf...  43.661112 -79.335613   
5  98, Bertmount Avenue, Leslieville, Toronto—Dan...  43.664839 -79.336175   
6  78, Galt Avenue, Leslieville, Toronto—Danforth...  43.668565 -79.336736   
7  Regatta Road, Toronto—Danforth, Old Toronto, T...  43.640269 -79.336968   
8  Unwin Avenue, Port Lands, Toronto—Danforth, Ol...  43.643994 -79.337530   
9  Basin Street, Toronto—Danforth, Old Toronto, T...  43.647719 -79.338091   

              X             Y  Distance from center  Restaurants in area  
0 -5.312327e+06  1.050182e+07           5992.495307                    0  
1 -5.311727e+06  1.050182e+07           5840.376700                    0  
2 -5.311127e+06  1.050182e+07           5747.173218                    0  
3 -5.310527e+06  1.050182e+07           5715.767665                    1  
4 -5.309927e+06  1.050182e+07           5747.173218                   11  
5 -5.309327e+06  1.050182e+07           5840.376700                    0  
6 -5.308727e+06  1.050182e+07           5992.495307                    6  
7 -5.313227e+06  1.050234e+07           5855.766389                    0  
8 -5.312627e+06  1.050234e+07           5604.462508                    0  
9 -5.312027e+06  1.050234e+07           5408.326913                    0

In [109]:
distances_to_chinese_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in chinese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_chinese_restaurant.append(min_distance)

df_locations['Distance to Chinese restaurant'] = distances_to_chinese_restaurant

In [110]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  Richard L. Hearn Thermal Generating Station (c...  43.646210 -79.333368   
1  Portlands Energy Centre, 470, Unwin Avenue, To...  43.649935 -79.333929   
2  Toronto Hydro, Commissioners Street, Toronto—D...  43.653661 -79.334490   
3  Revival Film Studios, 629, Eastern Avenue, Les...  43.657386 -79.335052   
4  67, Winnfred Avenue, Leslieville, Toronto—Danf...  43.661112 -79.335613   
5  98, Bertmount Avenue, Leslieville, Toronto—Dan...  43.664839 -79.336175   
6  78, Galt Avenue, Leslieville, Toronto—Danforth...  43.668565 -79.336736   
7  Regatta Road, Toronto—Danforth, Old Toronto, T...  43.640269 -79.336968   
8  Unwin Avenue, Port Lands, Toronto—Danforth, Ol...  43.643994 -79.337530   
9  Basin Street, Toronto—Danforth, Old Toronto, T...  43.647719 -79.338091   

              X             Y  Distance from center  Restaurants in area  \
0 -5.312327e+06  1.050182e+07           5992.495307                    0   
1 -5.311727e+06  1.050182e+07           5840.376700                    0   
2 -5.311127e+06  1.050182e+07           5747.173218                    0   
3 -5.310527e+06  1.050182e+07           5715.767665                    1   
4 -5.309927e+06  1.050182e+07           5747.173218                   11   
5 -5.309327e+06  1.050182e+07           5840.376700                    0   
6 -5.308727e+06  1.050182e+07           5992.495307                    6   
7 -5.313227e+06  1.050234e+07           5855.766389                    0   
8 -5.312627e+06  1.050234e+07           5604.462508                    0   
9 -5.312027e+06  1.050234e+07           5408.326913                    0   

   Distance to Chinese restaurant  
0                     2691.350575  
1                     2212.268283  
2                     1806.901766  
3                     1534.814982  
4                     1471.876376  
5                     1642.310294  
6                     1738.341764  
7                     3296.175085  
8                     2726.817418  
9                     2174.004661

In [111]:
print('Average distance to closest Chinese restaurant from each area center:', df_locations['Distance to Chinese restaurant'].mean())

Average distance to closest Chinese restaurant from each area center: 1392.4557724644678


OK, so on average Italian restaurant can be found within ~1400m from every area center candidate. That's fairly distant!

Let's crete a map showing heatmap / density of restaurants and try to extract some meaningfull info from that. 


In [112]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

chinese_latlons = [[res[2], res[3]] for res in chinese_restaurants.values()]

In [113]:
from folium import plugins
from folium.plugins import HeatMap

toronto_map = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(toronto_map) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
folium.Circle([latitude,longitude], radius=1000, fill=False, color='white').add_to(toronto_map)
folium.Circle([latitude,longitude], radius=2000, fill=False, color='white').add_to(toronto_map)
folium.Circle([latitude,longitude], radius=3000, fill=False, color='white').add_to(toronto_map)
toronto_map

Looks like a few pockets of low restaurant density closest to city center can be found north-east and south-east and from city Town Hall.

Let's create another heatmap map showing heatmap/density of Chinese restaurants only.


In [114]:
toronto_map = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(toronto_map) #cartodbpositron cartodbdark_matter
HeatMap(chinese_latlons).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
folium.Circle([latitude,longitude], radius=1000, fill=False, color='white').add_to(toronto_map)
folium.Circle([latitude,longitude], radius=2000, fill=False, color='white').add_to(toronto_map)
folium.Circle([latitude,longitude], radius=3000, fill=False, color='white').add_to(toronto_map)
toronto_map

This map is not so 'hot' (Chinese restaurants represent a subset of ~5% of all restaurants in Toronto) but it also indicates higher density of existing Chinese restaurants directly west from City Town Hall, with closest pockets of low Chinese restaurant density positioned east, south-east and north from city center.

Based on this we can see that there is still room in Downtown Toronto and Central Toronto. We will move the center of our area of interest and reduce it's size to have a radius of 2.5km. This keeps things interesting because we are fair close to the center, a high density place with a lot of potential customers.


In [123]:
roi_x_min = tor_x - 2500
roi_y_max = tor_y + 2500
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

toronto_map = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(toronto_map)
toronto_map

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)


This is nice, it covers all areas arroud Town Hall where we can fit a new restaurant.

Now we will repeat the process, gridding the area and to find the best candidates.

In [139]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

...

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

KeyboardInterrupt: 

In [125]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_chinese_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, chinese_restaurants)
    roi_chinese_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [126]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Chinese restaurant':roi_chinese_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  43.654884 -79.362508 -5.310577e+06  1.050504e+07                   3   
1  43.655505 -79.362602 -5.310477e+06  1.050504e+07                   3   
2  43.651410 -79.362731 -5.311127e+06  1.050513e+07                   0   
3  43.652031 -79.362825 -5.311027e+06  1.050513e+07                   1   
4  43.652652 -79.362919 -5.310927e+06  1.050513e+07                   1   
5  43.653273 -79.363013 -5.310827e+06  1.050513e+07                   1   
6  43.653894 -79.363107 -5.310727e+06  1.050513e+07                   1   
7  43.654515 -79.363202 -5.310627e+06  1.050513e+07                   4   
8  43.655136 -79.363296 -5.310527e+06  1.050513e+07                   4   
9  43.655757 -79.363390 -5.310427e+06  1.050513e+07                   4   

   Distance to Chinese restaurant  
0                      332.747183  
1                      316.598851  
2                      691.778848  
3                      598.391276  
4                      507.529570  
5                      420.832995  
6                      341.488733  
7                      275.914298  
8                      235.887356  
9                      234.855253

In [127]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_chn_distance = np.array(df_roi_locations['Distance to Chinese restaurant']>=400)
print('Locations with no Chinese restaurants within 400m:', good_chn_distance.sum())

good_locations = np.logical_and(good_res_count, good_chn_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 881
Locations with no Chinese restaurants within 400m: 1180
Locations with both conditions met: 625


In [128]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

toronto_map = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(toronto_map)
HeatMap(restaurant_latlons).add_to(toronto_map)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(toronto_map) 
toronto_map

In [129]:
toronto_map = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(toronto_map)
toronto_map

In [132]:
number_of_clusters = 10

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

toronto_map = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(toronto_map)
HeatMap(restaurant_latlons).add_to(toronto_map)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(toronto_map)
folium.Marker([latitude,longitude]).add_to(toronto_map)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(toronto_map) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(toronto_map)
toronto_map

<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-74-5d1352e10ce7>:16: DeprecationWarning: This

In [133]:
toronto_map = folium.Map(location=roi_center, zoom_start=14)
folium.Marker([latitude,longitude]).add_to(toronto_map)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(toronto_map)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(toronto_map)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(toronto_map) 
toronto_map

In [137]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = str(get_address(lat, lon)).replace(', Canada', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, tor_x, tor_y)
    print('{}{} => {:.1f}km from Toronto Town Hall'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis



<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


None                                               => 2.2km from Toronto Town Hall


<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


None                                               => 1.8km from Toronto Town Hall


...

<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


None                                               => 2.2km from Toronto Town Hall


<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


None                                               => 2.3km from Toronto Town Hall
None                                               => 1.0km from Toronto Town Hall


<ipython-input-74-5d1352e10ce7>:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


In [138]:
toronto_map = folium.Map(location=roi_center, zoom_start=14)
folium.Circle([latitude,longitude], radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(toronto_map)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(toronto_map) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(toronto_map)
toronto_map

## 4- Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Toronto (~1000 in our initial area of interest which was 12x12km around City Hall), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected south(east and west) and north from City Hall, so we focused our attention to areas south, south-east and north-east.

After directing our attention to this more narrow area of interest we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Chinese restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Chinese restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Toronto City Hall but not crowded with existing restaurants (particularly Chinese) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## 5- Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Toronto areas close to center with low number of restaurants (particularly Chinese restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Chinese restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis, and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

**Final decission on optimal restaurant location will be made by stakeholders** based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.